In [19]:
#Kraabime veebilehelt PDFid ja slaidiesitlused maha

import os
import requests
from urllib.parse import urljoin
from bs4 import BeautifulSoup
#Tegin siia meetodi, mis võtab nasdaqbalticu lehelt siis ISIN koodi ja kuupäeva järgi kõik .pdf formaadis failid,
#laeb need lokaalselt mulle alla.
def fetch_pdfs(ISIN,date):
    url = f"https://nasdaqbaltic.com/statistics/en/instrument/{ISIN}/reports?date={date}"
    #If there is no such folder, the script will create one automatically
    folder_location = r'C:\Users\marek.keskull\webscraping\lhv'
    if not os.path.exists(folder_location):os.mkdir(folder_location)

    response = requests.get(url)
    soup= BeautifulSoup(response.text, "html.parser")
    tr = soup.find("tbody")
    pdf2020 = tr.find("tr")
    
    for link in pdf2020.select("a[href$='.pdf']"):
        filename = os.path.join(folder_location,link['href'].split('/')[-1])
        with open(filename, 'wb') as f:
            f.write(requests.get(urljoin(url,link['href'])).content)
fetch_pdfs("EE3100073644","2021-01-11")

In [52]:
#kasutan tika libraryt, selle peab panema lokaalselt käima eraldi, et kasutada tika rest teenust.
import tika
from tika import parser

import os

folder_location = r'C:\Users\marek.keskull\webscraping\luminor\annual report'
#Võtan kõik allalaetud PDF'id ning muudan need .txt failideks, et mul jääks alles ainult plain text
def extract_text_from_pdfs_recursively(dir):
    for root, dirs, files in os.walk(dir):
        for file in files:
            path_to_pdf = os.path.join(root, file)
            [stem, ext] = os.path.splitext(path_to_pdf)
            if ext == '.pdf':
                print("Processing " + path_to_pdf)
                pdf_contents = parser.from_file(path_to_pdf)
                path_to_txt = stem + '.txt'
                with open(path_to_txt, 'w',encoding="utf-8") as txt_file:
                    print("Writing contents to " + path_to_txt)
                    txt_file.write(pdf_contents['content'])
                    


if __name__ == "__main__":
    extract_text_from_pdfs_recursively(folder_location)

Processing C:\Users\marek.keskull\webscraping\luminor\annual report\annual_report_2019_luminor.pdf
Writing contents to C:\Users\marek.keskull\webscraping\luminor\annual report\annual_report_2019_luminor.txt


In [35]:
import os
path = r'C:\Users\marek.keskull\webscraping\swedbank'
files = os.listdir(path)
print(files)
for file in files:
    path_to_pdf = os.path.join(path, file)
    [stem, ext] = os.path.splitext(path_to_pdf)
    if ext == '.txt':
        name , extension = path_to_pdf.split('swedbank\\')
        os.rename(os.path.join(path, file), os.path.join(path,'swedbank' + extension))

['Q1_20_eng.pdf', 'Q1_20_eng.txt', 'Q2_20_eng.pdf', 'Q2_20_eng.txt', 'Q3_20_eng.pdf', 'Q3_20_eng.txt']


In [53]:
quarters = []
path = r'C:\Users\marek.keskull\webscraping\annuals'
files = os.listdir(path)
for file in files:
    path_to_pdf = os.path.join(path, file)
    [stem, ext] = os.path.splitext(path_to_pdf)
    if ext == '.txt':
        quarters.append(file)
    

In [54]:
data = []
for c in quarters:
    with open(path+ "\\" + c, "rb") as file:
        text = file.read()
        asd = text.strip()
        decoded=str(asd,'utf-8')
        data.append(decoded)
data

['1 \r\n\r\nANNUAL REPORT 2019 \r\nLUMINOR HOLDING AS \r\n\r\nCONSOLIDATED FINANCIAL STATEMENTS  \r\n\r\nFOR THE YEAR ENDED 31 DECEMBER 2019 \r\n\r\n\r\n\r\nLuminor Holding AS Consolidated financial statements for the year ended 31 December 2019 \r\n\r\n2 \r\n\r\nCONTENTS \r\n\r\nGENERAL INFORMATION AND CONTACTS ............................................................................................................................................ 3 \r\n\r\nCEO STATEMENT.................................................................................................................................................................................. 4 \r\n\r\nMANAGEMENT REPORT ...................................................................................................................................................................... 5 \r\n\r\nCONSOLIDATED FINANCIAL STATEMENTS FOR THE YEAR ENDED 31 DECEMBER 2019 ....................................................................

In [55]:
#teen listidest dictionary
ddata = dict(zip(quarters, data))
ddata

{'annual_report_2019_luminor.txt': '1 \r\n\r\nANNUAL REPORT 2019 \r\nLUMINOR HOLDING AS \r\n\r\nCONSOLIDATED FINANCIAL STATEMENTS  \r\n\r\nFOR THE YEAR ENDED 31 DECEMBER 2019 \r\n\r\n\r\n\r\nLuminor Holding AS Consolidated financial statements for the year ended 31 December 2019 \r\n\r\n2 \r\n\r\nCONTENTS \r\n\r\nGENERAL INFORMATION AND CONTACTS ............................................................................................................................................ 3 \r\n\r\nCEO STATEMENT.................................................................................................................................................................................. 4 \r\n\r\nMANAGEMENT REPORT ...................................................................................................................................................................... 5 \r\n\r\nCONSOLIDATED FINANCIAL STATEMENTS FOR THE YEAR ENDED 31 DECEMBER 2019 ..................................

In [56]:
def combine_text(list_of_text):
    combined_text = ''.join(list_of_text)
    return combined_text

In [57]:
data_combined = {key: [combine_text(value)] for (key, value) in ddata.items()}

In [58]:
#pandas dataframe data
import pandas as pd
pd.set_option('max_colwidth',150)

data_df = pd.DataFrame.from_dict(data_combined).transpose()
data_df.columns = ['text']
data_df = data_df.sort_index()
data_df

text
annual_report_2019_luminor.txt  1 \r\n\r\nANNUAL REPORT 2019 \r\nLUMINOR HOLDING AS \r\n\r\nCONSOLIDATED FINANCIAL STATEMENTS  \r\n\r\nFOR THE YEAR ENDED 31 DECEMBER 2019 \r\n\r\...
lhv_annual_2019.txt             Group_annual_2019_T3.indd\r\n\r\n\r\nAS LHV Group\r\nConsolidated Annual Report 2019\r\n\r\n(Translation of the Estonian original)\r\n\r\n\r\n\r\n...
seb_annual_report_2019.txt      Annual ReportAnnua\r\nl R\r\n\r\ne\r\np\r\n\r\no\r\nrt 2\r\n\r\n0\r\n1\r\n\r\n9\r\n\r\n2019\r\n\r\n\r\n\r\nContents 2019 in brief\r\nImportant eve...
swedannual2019.txt              2019 \r\nAnnual and   \r\nSustainability Report\r\n\r\n\r\n\r\nFinancial information 2020\r\nQ1 Interim report  23 April\r\nQ2 Interim report  17 ...

# Andmete puhastamine


- Tekst kõik väikeste tähtedega
- Eemaldame punktid
- Eemaldame numbrid
- Eemdaldame ebavajaliku teksti, mis on kandiliste sulgude vahel


In [59]:
import re
import string

def clean_text_round1(text):
    text = text.lower()
    text = re.sub('\[.*?\]', '', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), ' ', text)
    text = re.sub('\w*\d\w*', '', text)
    
    return text

round1 = lambda x: clean_text_round1(x)

In [60]:
#vaatame puhastatud teksti
data_clean = pd.DataFrame(data_df.text.apply(round1))
data_clean



text
annual_report_2019_luminor.txt   \r\n\r\nannual report  \r\nluminor holding as \r\n\r\nconsolidated financial statements  \r\n\r\nfor the year ended  december  \r\n\r\n\r\n\r\nlu...
lhv_annual_2019.txt             group annual   indd\r\n\r\n\r\nas lhv group\r\nconsolidated annual report \r\n\r\n translation of the estonian original \r\n\r\n\r\n\r\nas lhv gro...
seb_annual_report_2019.txt      annual reportannua\r\nl r\r\n\r\ne\r\np\r\n\r\no\r\nrt \r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\ncontents  in brief\r\nimportant events and tren...
swedannual2019.txt               \r\nannual and   \r\nsustainability report\r\n\r\n\r\n\r\nfinancial information \r\n interim report   april\r\n interim report   july\r\n interim...

In [61]:
# 2. round puhastamisele
def clean_text_round2(text):
    text = re.sub('[‘’“”…]', '', text)
    text = re.sub('\n', '', text)
    #text = re.sub('https?://\S+|www\.\S+', '', text)
    #text = re.sub('<.*?>+', '', text)
    text = re.sub('\r', ' ', text)
    #text = re.sub(r"\s+"," ", text)
    #text = re.sub(r"^\s+", "", text)
    #text = re.sub(r"\s+[a-zA-Z]\s+", " ", text)
    #text = re.sub(r'/\d\.\s+|[a-z]\)\s+|•\s+|[A-Z]\.\s+|[IVX]+\.\s+/g', "",text)
    #text = re.sub(r'\xc2\xb7',"",text)
    text = re.sub(r'\W+', ' ', text)
    return text

round2 = lambda x: clean_text_round2(x)

In [62]:
#vaatame puhastatud teksti
data_clean = pd.DataFrame(data_clean.text.apply(round2))
data_clean


text
annual_report_2019_luminor.txt   annual report luminor holding as consolidated financial statements for the year ended december luminor holding as consolidated financial statemen...
lhv_annual_2019.txt             group annual indd as lhv group consolidated annual report translation of the estonian original as lhv group consolidated annual report consolidate...
seb_annual_report_2019.txt      annual reportannua l r e p o rt contents in brief important events and trends the global economy was fragile but gradually stabilised while centra...
swedannual2019.txt               annual and sustainability report financial information interim report april interim report july interim report october annual general meeting the...

In [63]:
import pickle
data_clean.to_pickle("annualpickles/annualcorpuses.pkl")

In [47]:
#moodustame document term matrix

from sklearn.feature_extraction.text import CountVectorizer

cv = CountVectorizer(stop_words='english')
data_cv = cv.fit_transform(data_clean.text)
data_dtm = pd.DataFrame(data_cv.toarray(), columns=cv.get_feature_names())
data_dtm.index = data_clean.index
data_dtm

ab  ability  accordance  according  accounting  \
swedbankQ1_20_eng.txt   5        1           2          2           3   
swedbankQ2_20_eng.txt   5        1           2          2           3   
swedbankQ3_20_eng.txt   5        1           2          2           3   

                       accrued  activities  added  additional  address  ...  \
swedbankQ1_20_eng.txt        2           3      1           3        1  ...   
swedbankQ2_20_eng.txt        2           3      1           3        1  ...   
swedbankQ3_20_eng.txt        2           3      1           3        1  ...   

                       undesirable  unexpected  uses  valuation  value  \
swedbankQ1_20_eng.txt            1           1     2          3      6   
swedbankQ2_20_eng.txt            1           1     2          3      6   
swedbankQ3_20_eng.txt            1           1     2          3      6   

                       various  volatility  website  www  year  
swedbankQ1_20_eng.txt        2           1        1    5     5  
swedbankQ2_20_eng.txt        2           1        1    4     5  
swedbankQ3_20_eng.txt        2           1        1    4     5  

[3 rows x 377 columns]

In [48]:
data = data_dtm.transpose()
data.head()

swedbankQ1_20_eng.txt  swedbankQ2_20_eng.txt  \
ab                              5                      5   
ability                         1                      1   
accordance                      2                      2   
according                       2                      2   
accounting                      3                      3   

            swedbankQ3_20_eng.txt  
ab                              5  
ability                         1  
accordance                      2  
according                       2  
accounting                      3

In [ ]:
# top 30 sõna sõnastikus
top_dict = {}
for c in data.columns:
    top = data[c].sort_values(ascending=False).head(30)
    top_dict[c]= list(zip(top.index, top.values))

top_dict

In [ ]:
import pickle
data_dtm.to_pickle("pickles/ignitisdtm.pkl")

In [ ]:
data_clean.to_pickle('pickles/ignitisdata_clean.pkl')
pickle.dump(cv, open("pickles/ignitiscv.pkl", "wb"))